# ASYNCHRONOUS PROGRAMMING: TASKS

 A Julia Task is a symmetric coroutine

In [1]:
t = @task begin; sleep(5); println("done"); end

Task (runnable) @0x00007f4ce9d81430

The task t can be run wheneveer we are ready


In [2]:
sleep(10)

In [3]:
istaskstarted(t)

false

 Add a Task to the scheduler's queue. This causes the task to run constantly when the system is otherwise idle, unless the task performs a blocking operation such as wait. Note that schedule returns immediately

In [4]:
schedule(t);

In [5]:
istaskdone(t)

false

Once the task has run, it is no longer runnable

In [6]:
schedule(t);

done


LoadError: schedule: Task not runnable

The wait function blocks the calling task until some other task finishes.

In [7]:
t = @task begin; sleep(2); println("done"); end

Task (runnable) @0x00007f4ce9fac740

In [8]:
s = @task begin; sleep(1); println("really done"); end

Task (runnable) @0x00007f4ce9fac8b0

In [9]:
schedule(t); schedule(s); wait(s);

really done


It is common to want to create a task and schedule it right away, so the macro @async is provided for that purpose

In [10]:
t = @async begin;    for i = 1:5  println("done")  end; end;

done
done
done
done
done


# ASYNCHRONOUS PROGRAMMING: CHANNELS

A Channel is a waitable first-in first-out queue which can have multiple tasks reading from and writing to it.

In [11]:
function producer(c::Channel)
           put!(c, "start")
           for n=1:4
               put!(c, 2n)
           end
           put!(c, "stop")
       end;

done


The Channel constructor accepts a 1-arg function as an argument,
   and wraps this function into a task, bound to the constructed channel.

In [12]:
chnl = Channel(producer);

One can then take! values repeatedly from the channel object:

In [13]:
take!(chnl)

"start"

In [14]:
take!(chnl)

2

In [15]:
take!(chnl)

4

In [16]:
take!(chnl)

6

In [17]:
take!(chnl)

8

In [18]:
take!(chnl)

"stop"

In [19]:
take!(chnl)

LoadError: InvalidStateException("Channel is closed.", :closed)

The channel object is closed automatically when the task terminates.

In [20]:
for x in Channel(producer)
                  println(x)
              end

start
2
4
6
8
stop


A channel can be visualized as a pipe, i.e., it has a write end and a read end.

In [21]:
function producer(c::Channel)
       for i=0:4
           put!(c, i+1)
       end	   
end

producer (generic function with 1 method)

In [22]:
c1 = Channel(producer)

Channel{Any}(0) (1 item available)

In [23]:
function consumer(c::Channel)
       while isready(c1)
           data = take!(c1)
	   result = data^2
	   put!(c,result)
	end
end

consumer (generic function with 1 method)

In [24]:
c2 = Channel(consumer)

Channel{Any}(0) (1 item available)

In [25]:
isready(c2)

true

In [26]:
take!(c2)

1

In [27]:
isready(c2)

true

In [28]:
take!(c2)

4

In [29]:
isready(c2)

true

In [30]:
take!(c2)

9

In [31]:
isready(c2)

true

In [32]:
take!(c2)

16

In [33]:
isready(c2)

true

In [34]:
take!(c2)

25

In [35]:
isready(c2)

false

# DISTRIBUTED COMPUTING: remote calls and remote references

 The first argument to remotecall is the function to call.
The second argument to remotecall is the id of the process that will do the work, and the remaining arguments will be passed to the function being called

In [36]:
using Distributed
addprocs(4)

4-element Vector{Int64}:
 2
 3
 4
 5

In [37]:
r = remotecall(rand, 2, 2, 2)

Future(2, 1, 6, ReentrantLock(nothing, Base.GenericCondition{Base.Threads.SpinLock}(Base.InvasiveLinkedList{Task}(nothing, nothing), Base.Threads.SpinLock(0)), 0), nothing)

In [38]:
s = @spawnat 2 1 .+ fetch(r)

Future(2, 1, 7, ReentrantLock(nothing, Base.GenericCondition{Base.Threads.SpinLock}(Base.InvasiveLinkedList{Task}(nothing, nothing), Base.Threads.SpinLock(0)), 0), nothing)

In [39]:
fetch(s)

2×2 Matrix{Float64}:
 1.71554  1.0451
 1.1314   1.36308

In [40]:
remotecall_fetch(r-> fetch(r)[1, 1], 2, r)

0.7155425812447143

To make things easier, the symbol :any can be passed to @spawnat, which picks where to do the operation

In [41]:
r = @spawnat :any rand(2,2)

Future(2, 1, 10, ReentrantLock(nothing, Base.GenericCondition{Base.Threads.SpinLock}(Base.InvasiveLinkedList{Task}(nothing, nothing), Base.Threads.SpinLock(0)), 0), nothing)

In [42]:
s = @spawnat :any 1 .+ fetch(r)

Future(3, 1, 11, ReentrantLock(nothing, Base.GenericCondition{Base.Threads.SpinLock}(Base.InvasiveLinkedList{Task}(nothing, nothing), Base.Threads.SpinLock(0)), 0), nothing)

In [43]:
fetch(s)

2×2 Matrix{Float64}:
 1.2142   1.9413
 1.12452  1.62971

Code must be available on any process that runs

In [44]:
function rand2(dims...)
           return 2*rand(dims...)
       end

rand2 (generic function with 1 method)

In [45]:
rand2(2,2)

2×2 Matrix{Float64}:
 0.782975  0.594535
 0.741954  1.15837

In [46]:
fetch(@spawnat :any rand2(2,2))

LoadError: On worker 4:
UndefVarError: #rand2 not defined
Stacktrace:
  [1] [0m[1mdeserialize_datatype[22m
[90m    @ [39m[90m/mnt/storage/data/share/julia/julia-1.7.1/julia-1.7.1/share/julia/stdlib/v1.7/Serialization/src/[39m[90m[4mSerialization.jl:1332[24m[39m
  [2] [0m[1mhandle_deserialize[22m
[90m    @ [39m[90m/mnt/storage/data/share/julia/julia-1.7.1/julia-1.7.1/share/julia/stdlib/v1.7/Serialization/src/[39m[90m[4mSerialization.jl:854[24m[39m
  [3] [0m[1mdeserialize[22m
[90m    @ [39m[90m/mnt/storage/data/share/julia/julia-1.7.1/julia-1.7.1/share/julia/stdlib/v1.7/Serialization/src/[39m[90m[4mSerialization.jl:801[24m[39m
  [4] [0m[1mhandle_deserialize[22m
[90m    @ [39m[90m/mnt/storage/data/share/julia/julia-1.7.1/julia-1.7.1/share/julia/stdlib/v1.7/Serialization/src/[39m[90m[4mSerialization.jl:861[24m[39m
  [5] [0m[1mdeserialize[22m
[90m    @ [39m[90m/mnt/storage/data/share/julia/julia-1.7.1/julia-1.7.1/share/julia/stdlib/v1.7/Seri

In [47]:
@everywhere function rand2(dims...)
           return 2*rand(dims...)
       end


In [48]:
fetch(@spawnat :any rand2(2,2))

2×2 Matrix{Float64}:
 0.35735  0.664926
 1.642    0.329798

Sending messages and moving data constitute most of the overhead in a distributed program.

In [49]:
A = rand(1000,1000);

In [50]:
Bref = @spawnat :any A^2;

In [51]:
fetch(Bref);

Alternatively:

In [52]:
Bref = @spawnat :any rand(1000,1000)^2;

In [53]:
fetch(Bref);

Fortunately, many useful parallel computations do not require data movement. 

In [54]:
@everywhere function count_heads(n)
           c::Int = 0
           for i = 1:n
               c += rand(Bool)
           end
           c
       end

In [55]:
a = @spawnat :any count_heads(100000000)

Future(4, 1, 37, ReentrantLock(nothing, Base.GenericCondition{Base.Threads.SpinLock}(Base.InvasiveLinkedList{Task}(nothing, nothing), Base.Threads.SpinLock(0)), 0), nothing)

In [56]:
b = @spawnat :any count_heads(100000000)

Future(5, 1, 38, ReentrantLock(nothing, Base.GenericCondition{Base.Threads.SpinLock}(Base.InvasiveLinkedList{Task}(nothing, nothing), Base.Threads.SpinLock(0)), 0), nothing)

In [57]:
fetch(a)+fetch(b)

100010248

The  construction below implements the pattern of assigning iterations to multiple processes, and combining them with a specified reduction (in this case (+)). The result of each iteration is taken as the value of the last expression inside the loop. The whole parallel loop expression itself evaluates to the final answer.

In [58]:
nheads = @distributed (+) for i = 1:200000000
    Int(rand(Bool))
end

100005849

Note that although parallel for loops look like serial for loops, their behavior is dramatically different. In particular, the iterations do not happen in a specified order, and writes to variables or arrays will not be globally visible since iterations run on different processes. Any variables used inside the parallel loop will be copied and broadcast to each process.

In [59]:
a = zeros(100000)

100000-element Vector{Float64}:
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 ⋮
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0

In [60]:
@distributed for i = 1:100000
           a[i] = i
       end

Task (runnable) @0x00007f4cea44fde0

In [61]:
a[1]

0.0

In [62]:
a[2]

0.0

Fortunately, Julia has SharedArrays for solving the above issue

In [63]:
using SharedArrays

In [64]:
a = SharedArray{Float64}(10)
@distributed for i = 1:10
    a[i] = i
end

Task (runnable) @0x00007f4ce8f13b00

In [65]:
a[1]

1.0

In [66]:
a[2]

2.0

The Fib example in parallel with Julia

In [67]:
@everywhere function fib(n)
                               if (n < 2) 
                                   return n
                               else return fib(n-1) + fib(n-2)
                               end
                            end

In [68]:
z = @spawn fib(10)

Future(2, 1, 78, ReentrantLock(nothing, Base.GenericCondition{Base.Threads.SpinLock}(Base.InvasiveLinkedList{Task}(nothing, nothing), Base.Threads.SpinLock(0)), 0), nothing)

In [69]:
fetch(z)

55

In [70]:
@time [fib(i) for i=1:45];

 13.432560 seconds (50.42 k allocations: 2.670 MiB, 0.19% compilation time)


In [71]:
@everywhere function fib_parallel(n)
                        if (n < 40) 
                            return fib(n)
                        else 
                            x = @spawn fib_parallel(n-1) 
                            y = fib_parallel(n-2)
                            return fetch(x) + y
                        end
                     end

In [72]:
@time [fib_parallel(i) for i=1:42];

  4.921348 seconds (269.85 k allocations: 14.777 MiB, 1.59% compilation time)


In [73]:
@time [fib_parallel(i) for i=1:45];

  8.094894 seconds (336.84 k allocations: 17.752 MiB, 2.32% compilation time)


In [74]:
@time [fib(45) for i=1:4]

 21.316801 seconds (46.68 k allocations: 2.465 MiB, 0.13% compilation time)


4-element Vector{Int64}:
 1134903170
 1134903170
 1134903170
 1134903170

In [75]:
@time [fib_parallel(45) for i=1:4]

 10.186788 seconds (54.86 k allocations: 2.991 MiB, 0.32% compilation time)


4-element Vector{Int64}:
 1134903170
 1134903170
 1134903170
 1134903170